#### Monday, January 13, 2025

This all runs with the 4090.

In [1]:
# only target the 4090 ...
import os
os.environ["CUDA_VISIBLE_DEVICES"]="0"

# Preference Alignment with Odds Ratio Preference Optimization (ORPO)

This notebook will guide you through the process of fine-tuning a language model using Odds Ratio Preference Optimization (ORPO). We will use the SmolLM2-135M model which has **not** been through SFT training, so it is not compatible with DPO. This means, you cannot use the model you trained in [1_instruction_tuning](../../1_instruction_tuning/notebooks/sft_finetuning_example.ipynb).

<div style='background-color: lightblue; padding: 10px; border-radius: 5px; margin-bottom: 20px; color:black'>
     <h2 style='margin: 0;color:blue'>Exercise: Aligning SmolLM2 with ORPOTrainer</h2>
     <p>Take a dataset from the Hugging Face hub and align a model on it. </p> 
     <p><b>Difficulty Levels</b></p>
     <p>🐢 Use the `trl-lib/ultrafeedback_binarized` dataset</p>
     <p>🐕 Try out the `argilla/ultrafeedback-binarized-preferences` dataset</p>
     <p>🦁 Try on a subset of mlabonne's `orpo-dpo-mix-40k` dataset</p>
</div>



## Import libraries


In [2]:
import torch
import os
from datasets import load_dataset
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
)
from trl import ORPOConfig, ORPOTrainer, setup_chat_format

In [3]:
# Authenticate to Hugging Face
from huggingface_hub import login

login()

Token has not been saved to git credential helper.


## Format dataset

In [4]:
# Load dataset

# TODO: 🦁🐕 change the dataset to one of your choosing
dataset = load_dataset(path="trl-lib/ultrafeedback_binarized")

In [5]:
# TODO: 🐕 If your dataset is not represented as conversation lists, you can use the `process_dataset` function to convert it.

## Define the model

In [6]:
model_name = "HuggingFaceTB/SmolLM2-135M"

device = (
    "cuda"
    if torch.cuda.is_available()
    else "mps" if torch.backends.mps.is_available() else "cpu"
)
device

'cuda'

In [7]:
# Model to fine-tune
model = AutoModelForCausalLM.from_pretrained(
    pretrained_model_name_or_path=model_name,
    torch_dtype=torch.float32,
).to(device)
model.config.use_cache = False
tokenizer = AutoTokenizer.from_pretrained(model_name)
model, tokenizer = setup_chat_format(model, tokenizer)

config.json:   0%|          | 0.00/704 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/269M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/111 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/3.66k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/801k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/466k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.10M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/831 [00:00<?, ?B/s]

In [8]:
# Set our name for the finetune to be saved &/ uploaded to
finetune_name = "SmolLM2-FT-ORPO"
finetune_tags = ["smol-course", "module_1"]

## Train model with ORPO

In [9]:
orpo_args = ORPOConfig(
    # Small learning rate to prevent catastrophic forgetting
    learning_rate=8e-6,
    # Linear learning rate decay over training
    lr_scheduler_type="linear",
    # Maximum combined length of prompt + completion
    max_length=1024,
    # Maximum length for input prompts
    max_prompt_length=512,
    # Controls weight of the odds ratio loss (λ in paper)
    beta=0.1,
    # Batch size for training
    per_device_train_batch_size=2,
    per_device_eval_batch_size=2,
    # Helps with training stability by accumulating gradients before updating
    gradient_accumulation_steps=4,
    # Memory-efficient optimizer for CUDA, falls back to adamw_torch for CPU/MPS
    optim="paged_adamw_8bit" if device == "cuda" else "adamw_torch",
    # Number of training epochs
    num_train_epochs=1,
    # When to run evaluation
    evaluation_strategy="steps",
    # Evaluate every 20% of training
    eval_steps=0.2,
    # Log metrics every step
    logging_steps=1,
    # Gradual learning rate warmup
    warmup_steps=10,
    # Disable external logging
    report_to="none",
    # Where to save model/checkpoints
    output_dir="./results/",
    # Enable MPS (Metal Performance Shaders) if available
    use_mps_device=device == "mps",
    hub_model_id=finetune_name,
)

/home/rob/Data/Documents/Github/rkaunismaa/smol-course/.venv/lib/python3.11/site-packages/transformers/training_args.py:1568: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [10]:
# This does not use the GPU
trainer = ORPOTrainer(
    model=model,
    args=orpo_args,
    train_dataset=dataset["train"],
    eval_dataset=dataset["test"],
    processing_class=tokenizer,
)

# 3m 20.6s on KAUWITB

/home/rob/Data/Documents/Github/rkaunismaa/smol-course/.venv/lib/python3.11/site-packages/trl/trainer/orpo_trainer.py:276: UserWarning: When using DPODataCollatorWithPadding, you should set `remove_unused_columns=False` in your TrainingArguments we have set it for you, but you should do it yourself in the future.
  warnings.warn(


Map:   0%|          | 0/62135 [00:00<?, ? examples/s]

Map:   0%|          | 0/62135 [00:00<?, ? examples/s]

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

In [11]:
trainer.train()  # Train the model

# 78m 42.6s on the 4090

  0%|          | 0/7767 [00:00<?, ?it/s]

Could not estimate the number of tokens of the input, floating-point operations will not be computed


{'loss': 2.2484, 'grad_norm': 12.79349422454834, 'learning_rate': 8e-07, 'rewards/chosen': -0.1963876187801361, 'rewards/rejected': -0.1509920060634613, 'rewards/accuracies': 0.5, 'rewards/margins': -0.045395627617836, 'logps/rejected': -1.5099201202392578, 'logps/chosen': -1.9638762474060059, 'logits/rejected': 10.306058883666992, 'logits/chosen': 12.686930656433105, 'nll_loss': 2.126336097717285, 'log_odds_ratio': -1.2202308177947998, 'log_odds_chosen': -0.5531083941459656, 'epoch': 0.0}
{'loss': 2.4573, 'grad_norm': 10.085844993591309, 'learning_rate': 1.6e-06, 'rewards/chosen': -0.3073978126049042, 'rewards/rejected': -0.23975682258605957, 'rewards/accuracies': 0.5, 'rewards/margins': -0.06764098256826401, 'logps/rejected': -2.3975682258605957, 'logps/chosen': -3.0739779472351074, 'logits/rejected': 14.947060585021973, 'logits/chosen': 11.702362060546875, 'nll_loss': 2.307814598083496, 'log_odds_ratio': -1.4951130151748657, 'log_odds_chosen': -0.637850821018219, 'epoch': 0.0}
{'los

  0%|          | 0/500 [00:00<?, ?it/s]

{'eval_loss': 1.913982629776001, 'eval_runtime': 22.5936, 'eval_samples_per_second': 44.26, 'eval_steps_per_second': 22.13, 'eval_rewards/chosen': -0.1523517370223999, 'eval_rewards/rejected': -0.16538527607917786, 'eval_rewards/accuracies': 0.5239999890327454, 'eval_rewards/margins': 0.01303353626281023, 'eval_logps/rejected': -1.6538525819778442, 'eval_logps/chosen': -1.523517370223999, 'eval_logits/rejected': 8.142281532287598, 'eval_logits/chosen': 7.47804594039917, 'eval_nll_loss': 1.8404940366744995, 'eval_log_odds_ratio': -0.7348864674568176, 'eval_log_odds_chosen': 0.1569509655237198, 'epoch': 0.2}
{'loss': 1.6519, 'grad_norm': 4.982922077178955, 'learning_rate': 6.406600489880108e-06, 'rewards/chosen': -0.14299142360687256, 'rewards/rejected': -0.1279604732990265, 'rewards/accuracies': 0.375, 'rewards/margins': -0.01503094844520092, 'logps/rejected': -1.2796047925949097, 'logps/chosen': -1.4299143552780151, 'logits/rejected': 6.910728454589844, 'logits/chosen': 7.1273880004882

...

  0%|          | 0/500 [00:00<?, ?it/s]

{'eval_loss': 1.8658835887908936, 'eval_runtime': 22.5799, 'eval_samples_per_second': 44.287, 'eval_steps_per_second': 22.144, 'eval_rewards/chosen': -0.1480764001607895, 'eval_rewards/rejected': -0.1598084270954132, 'eval_rewards/accuracies': 0.5249999761581421, 'eval_rewards/margins': 0.011732026003301144, 'eval_logps/rejected': -1.5980842113494873, 'eval_logps/chosen': -1.4807639122009277, 'eval_logits/rejected': 7.322296619415283, 'eval_logits/chosen': 6.770627498626709, 'eval_nll_loss': 1.79215669631958, 'eval_log_odds_ratio': -0.7372671961784363, 'eval_log_odds_chosen': 0.144988015294075, 'epoch': 0.6}
{'loss': 2.2215, 'grad_norm': 6.117021560668945, 'learning_rate': 3.20123759185252e-06, 'rewards/chosen': -0.17971275746822357, 'rewards/rejected': -0.14339853823184967, 'rewards/accuracies': 0.25, 'rewards/margins': -0.0363142304122448, 'logps/rejected': -1.4339853525161743, 'logps/chosen': -1.797127604484558, 'logits/rejected': 7.375786781311035, 'logits/chosen': 7.77734661102294

  0%|          | 0/500 [00:00<?, ?it/s]

{'eval_loss': 1.857668399810791, 'eval_runtime': 22.6981, 'eval_samples_per_second': 44.057, 'eval_steps_per_second': 22.028, 'eval_rewards/chosen': -0.14742349088191986, 'eval_rewards/rejected': -0.1590179204940796, 'eval_rewards/accuracies': 0.5260000228881836, 'eval_rewards/margins': 0.011594420298933983, 'eval_logps/rejected': -1.5901790857315063, 'eval_logps/chosen': -1.4742348194122314, 'eval_logits/rejected': 7.202993392944336, 'eval_logits/chosen': 6.673868179321289, 'eval_nll_loss': 1.783944845199585, 'eval_log_odds_ratio': -0.7372371554374695, 'eval_log_odds_chosen': 0.144301638007164, 'epoch': 0.8}
{'loss': 1.7883, 'grad_norm': 5.934208393096924, 'learning_rate': 1.5985561428387263e-06, 'rewards/chosen': -0.16214077174663544, 'rewards/rejected': -0.19535760581493378, 'rewards/accuracies': 0.375, 'rewards/margins': 0.03321682661771774, 'logps/rejected': -1.9535760879516602, 'logps/chosen': -1.6214078664779663, 'logits/rejected': 8.805728912353516, 'logits/chosen': 7.851108551

TrainOutput(global_step=7767, training_loss=1.8793173650371011, metrics={'train_runtime': 4722.5275, 'train_samples_per_second': 13.157, 'train_steps_per_second': 1.645, 'total_flos': 0.0, 'train_loss': 1.8793173650371011, 'epoch': 1.0})

In [12]:
# Save the model
trainer.save_model(f"./{finetune_name}")

In [13]:
# Save to the huggingface hub if login (HF_TOKEN is set)
if os.getenv("HF_TOKEN") and False:
    trainer.push_to_hub(tags=finetune_tags)

## 💐 You're done!

This notebook provided a step-by-step guide to fine-tuning the `HuggingFaceTB/SmolLM2-135M` model using the `ORPOTrainer`. By following these steps, you can adapt the model to perform specific tasks more effectively. If you want to carry on working on this course, here are steps you could try out:

- Try this notebook on a harder difficulty
- Review a colleagues PR
- Improve the course material via an Issue or PR.